In [ ]:
import pygame, random, math, numpy as np

In [ ]:
class PVector:
    def __init__(self, x, y):
        self.x = x
        self.y = y

    def add(self, other):
        return PVector(self.x + other.x, self.y + other.y)

    def sub(self, other):
        return PVector(self.x - other.x, self.y - other.y)

    def mult(self, scalar):
        return PVector(self.x * scalar, self.y * scalar)

    def mag(self):
        return math.sqrt(self.x**2 + self.y**2)

    def normalize(self):
        magnitude = self.mag()
        if magnitude != 0:
            return self.mult(1 / magnitude)
        else:
            return PVector(0, 0)

In [ ]:
def map_value(value, start1, stop1, start2, stop2):
    return start2 + abs(stop2 - start2) * ((value - start1) / abs(stop1 - start1))

In [ ]:
# particle params
particles = []
simulation_rate = 0.01
repulsive_factor = -3
friction = 0.85
numTypes = 6

# simulation params
width, height = 800, 600

In [ ]:
forces = [[0.0] * numTypes for _ in range(numTypes)]
minDistance = [[0.0] * numTypes for _ in range(numTypes)]
radius = [[0.0] * numTypes for _ in range(numTypes)]
colors = [(26, 46, 175), (65, 115, 227), (106, 227, 238), (234, 179, 79), (216, 66, 33), (216, 10, 33)]

def setParams():
    for i in range(numTypes):
        for j in range(numTypes):
            difference = np.linalg.norm(i - j) 
            forces[i][j] = map_value(1 / (difference * i + 1), 0, 1, 0.3, 1.5)
            minDistance[i][j] = map_value(i + j, 0, 10, 50, 10)
            radius[i][j] = map_value(i, 0, 5, 70, 140)

setParams()

In [ ]:
class Particle:
    def __init__(self, type):
        self.position = PVector(random.uniform(0, width), random.uniform(0, height))
        self.velocity = PVector(0, 0)
        self.type = type

    def update(self):
        direction = PVector(0, 0)
        totalForce = PVector(0, 0)
        acceleration = PVector(0, 0)
        distance = 0.0
        for particle in particles:
            if particle != self:
                direction = self.position.sub(particle.position)

                # calculate shorter distance
                if (direction.x > width / 2):
                    direction.x -= width
                if (direction.x < -width / 2):
                    direction.x += width
                if (direction.y > height / 2):
                    direction.y -= height
                if (direction.y < -height / 2):
                    direction.y += height

                distance = direction.mag()
                direction = direction.normalize()
                if distance < minDistance[self.type][particle.type]:
                    force = direction
                    force = force.mult(abs(forces[self.type][particle.type])*(repulsive_factor))
                    force = force.mult(map_value(distance, 0, minDistance[self.type][particle.type], 1, 0))
                    force = force.mult(simulation_rate)
                    totalForce = totalForce.add(force)
                    
                if distance < radius[self.type][particle.type]:
                    force = direction
                    force = force.mult(forces[self.type][particle.type])
                    force = force.mult(map_value(distance, 0, radius[self.type][particle.type], 1, 0))
                    force = force.mult(simulation_rate)
                    totalForce = totalForce.add(force)
                    
        acceleration = acceleration.add(totalForce.mult(0.5))
        self.velocity = self.velocity.add(acceleration)
        self.position = self.position.add(self.velocity)
        self.position.x = (self.position.x + width) % width
        self.position.y = (self.position.y + height) % height
        self.velocity.mult(friction)


In [ ]:
class Button:
    def __init__(self, x, y, width, height, color, text, text_color):
        self.rect = pygame.Rect(x, y, width, height)
        self.color = color
        self.text = text
        self.text_color = text_color

    def draw(self, surface):
        pygame.draw.rect(surface, self.color, self.rect)
        font = pygame.font.Font(None, 36)
        text = font.render(self.text, True, self.text_color)
        text_rect = text.get_rect(center=self.rect.center)
        surface.blit(text, text_rect)

    def is_clicked(self, pos):
        return self.rect.collidepoint(pos)

In [ ]:
# params
num_particles = 150
particles = [Particle(random.randint(0, numTypes - 1)) for _ in range(num_particles)]

# setup
pygame.init()
width, height = 800, 600
screen = pygame.display.set_mode((width, height))
pygame.display.set_caption("Particle Simulation")

# start button
button_width = 70
button_height = 30
button_x = width - button_width - 10
button_y = height - button_height - 10
button = Button(button_x, button_y, button_width, button_height, (86, 191, 65), "Start", (255, 255, 255))
simulation_running = False

# run sim
running = True
while running:
    for event in pygame.event.get():
        if event.type == pygame.QUIT:
            running = False
        elif event.type == pygame.MOUSEBUTTONDOWN:
            if button.is_clicked(event.pos):
                simulation_running = not simulation_running

    if simulation_running:
        for particle in particles:
            particle.update()

    screen.fill((255, 255, 255))
    for particle in particles:
        pygame.draw.circle(screen, colors[particle.type], (int(particle.position.x), int(particle.position.y)), 5)

    legend_x = 20
    legend_y = 20
    legend_spacing = 20
    particle_names = ["Introvert", "---", "---", "---", "---", "Extrovert"]
    for particle_type in range(numTypes):
        pygame.draw.circle(screen, colors[particle_type], (legend_x, legend_y), 5)
        pygame.draw.rect(screen, (255, 255, 255), (legend_x + 10, legend_y - 5, 100, 20))
        font = pygame.font.Font(None, 20)
        text = font.render(f"{particle_names[particle_type]}", True, (0, 0, 0))
        screen.blit(text, (legend_x + 15, legend_y - 5))
        legend_y += legend_spacing
        
    button.draw(screen)
    pygame.display.flip()

pygame.quit()